# TF Serving connect

In [3]:
!which pip

/home/erick/miniconda3/envs/ml-zoomcamp/bin/pip


In [43]:
%%capture
!pip install tensorflow-serving-api

In [1]:
from keras_image_helper import create_preprocessor
import tensorflow as tf
from tensorflow_serving.apis import predict_pb2, prediction_service_pb2_grpc
import grpc

2023-11-14 22:52:59.515988: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-11-14 22:52:59.703525: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-11-14 22:52:59.703602: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-11-14 22:52:59.703654: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-11-14 22:52:59.807854: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-11-14 22:52:59.809796: I tensorflow/core/platform/cpu_feature_guard.cc:182] This Tens

In [2]:
preprocessor = create_preprocessor('xception', target_size=(299,299))
X = preprocessor.from_path('pants.png')

In [3]:
host = 'localhost:8500'
channel = grpc.insecure_channel(host)

In [4]:
stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)

In [5]:
def np_to_protobuf(data):
    return tf.make_tensor_proto(data.tolist(), shape=data.shape)

In [6]:
pb_request = predict_pb2.PredictRequest()
pb_request.model_spec.name = 'clothing-model'
pb_request.model_spec.signature_name = 'serving_default'
pb_request.inputs['input_20'].CopyFrom(np_to_protobuf(X))

In [7]:
pb_request

model_spec {
  name: "clothing-model"
  signature_name: "serving_default"
}
inputs {
  key: "input_20"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 299
      }
      dim {
        size: 299
      }
      dim {
        size: 3
      }
    }
    tensor_content: "\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\200?\000\000\2

In [8]:
pb_response = stub.Predict(pb_request, timeout=30.0)

In [9]:
classes = [
    'dress',
    'hat',
    'longsleeve',
	'outwear',
    'pants',
	'shirt',
    'shoes',
    'shorts',
    'skirt',
    't-shirt']

In [10]:
predictions = pb_response.outputs['dense_19'].float_val
sorted(zip(classes, predictions), key=lambda x:-x[1])

[('pants', 7.054928779602051),
 ('shorts', 1.9362751245498657),
 ('outwear', 1.1031335592269897),
 ('shirt', 0.9493517875671387),
 ('longsleeve', -1.272936224937439),
 ('dress', -1.7161682844161987),
 ('shoes', -2.3776519298553467),
 ('hat', -2.463102340698242),
 ('t-shirt', -3.1740787029266357),
 ('skirt', -3.668224334716797)]

Using Rest-ful

In [20]:
import json
import requests

jsondata = {
    "signature_name": "serving_default",
    "instances": X.tolist()
}

data = json.dumps(jsondata)

heads = {
    "content-type": "application/json"
}

url = "http://localhost:8501/v1/models/clothing-model:predict"
response = requests.post(url, data = data, headers = heads)
predictions = response.json()['predictions'][0]

print(predictions)

[-1.71616828, -2.46310234, -1.27293622, 1.10313356, 7.05492878, 0.949351788, -2.37765193, 1.93627512, -3.66822433, -3.1740787]


In [19]:
sorted(zip(classes, predictions), key=lambda x: -x[1])

[('pants', 7.05492878),
 ('shorts', 1.93627512),
 ('outwear', 1.10313356),
 ('shirt', 0.949351788),
 ('longsleeve', -1.27293622),
 ('dress', -1.71616828),
 ('shoes', -2.37765193),
 ('hat', -2.46310234),
 ('t-shirt', -3.1740787),
 ('skirt', -3.66822433)]